# models for opcode frequency

## Import Libraries

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import os
import time
import json
import pandas as pd
from pathlib import Path
import joblib

import optuna
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.neural_network import MLPClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.multiclass import OneVsRestClassifier


## Const

In [3]:
PATH = Path.cwd().parents[1]
DATA_PATH = os.path.join(PATH, 'data/processed')
MODEL_PATH = os.path.join(PATH, 'models')

In [4]:
with open(os.path.join(DATA_PATH, 'feature-opcode-freq_list.json')) as f:
    feature_list = json.load(f)

with open(os.path.join(DATA_PATH, 'labels-opcode-freq.json')) as f:
    labels = json.load(f)

In [5]:
train_df = pd.read_csv(os.path.join(DATA_PATH, 'train-opcode-freq.csv'))
test_df = pd.read_csv(os.path.join(DATA_PATH, 'test-opcode-freq.csv'))

X_train = train_df[feature_list]
y_train = train_df[labels]

X_test = test_df[feature_list]
y_test = test_df[labels]

In [6]:
X_train.head()

PUSH1  MSTORE  CALLDATASIZE  LT  PUSH2  JUMPI  CALLDATALOAD  PUSH29  SWAP1  \
0      1       0             2   0      0      1             0       0      1   
1     16       2             2   0      0      2             1       0      0   
2     40       5             5   2     32     10             2       0      7   
3     53       7             5   2     43      9             2       0      8   
4    178      32             7   7    134     41             6       0     66   

   DIV  ...  UNKNOWN_0xc6  UNKNOWN_0xe1  INVALID_0x70  PUSH30  DUP16  \
0    0  ...             0             0             0       0      0   
1    0  ...             0             0             0       0      0   
2    0  ...             0             0             0       0      1   
3    0  ...             0             0             0       0      0   
4    0  ...             0             0             0       0      0   

   UNKNOWN_0x2b  UNKNOWN_0xd8  INVALID_0x7a  UNKNOWN_0xf9  INVALID_0x7f  
0             0             0             0             0             0  
1             0             0             0             0             0  
2             1             0             0             0             0  
3             0             0             0             0             0  
4             0             0             0             0             0  

[5 rows x 265 columns]

In [7]:
y_train.head()

mint  leak  limit
0     0     0      0
1     0     0      0
2     0     0      0
3     0     0      0
4     0     0      0

## Traditional Machine Learning Models

In [8]:
models = {
    "Logistic Regression": OneVsRestClassifier(LogisticRegression(max_iter=1000)),
    "Random Forest": OneVsRestClassifier(RandomForestClassifier()),
    "Gradient Boosting": OneVsRestClassifier(GradientBoostingClassifier()),
    "AdaBoost": OneVsRestClassifier(AdaBoostClassifier()),
    "SVM (Linear)": OneVsRestClassifier(SVC(kernel="linear")),
    "KNN": OneVsRestClassifier(KNeighborsClassifier()),
    "Naive Bayes": OneVsRestClassifier(GaussianNB()),
    "MLP Classifier": OneVsRestClassifier(MLPClassifier(max_iter=300)),
    "XGBoost": OneVsRestClassifier(XGBClassifier(use_label_encoder=False, eval_metric='logloss')),
    "LightGBM": OneVsRestClassifier(LGBMClassifier()),
    "DecisionTree": OneVsRestClassifier(DecisionTreeClassifier())
}

In [9]:
results = []

for name, model in models.items():
    start = time.time()
    model.fit(X_train, y_train)
    end = time.time()

    y_pred = model.predict(X_test)

    results.append({
        "Classifier": name,
        "Accuracy": accuracy_score(y_test, y_pred),
        "Precision": precision_score(y_test, y_pred, average="macro"),  # change to 'macro' if multi-class
        "Recall": recall_score(y_test, y_pred, average="macro"),
        "F1-Score": f1_score(y_test, y_pred, average="macro"),
        "Training Time": round(end - start, 3)
    })

[LightGBM] [Info] Number of positive: 39, number of negative: 98
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000374 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1889
[LightGBM] [Info] Number of data points in the train set: 137, number of used features: 94
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.284672 -> initscore=-0.921406
[LightGBM] [Info] Start training from score -0.921406
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best 

### Result

In [10]:
df = pd.DataFrame(results)
df.sort_values(by="F1-Score", ascending=False, inplace=True)
df

Classifier  Accuracy  Precision    Recall  F1-Score  \
9              LightGBM  0.428571   0.888889  0.388889  0.484127   
5                   KNN  0.285714   0.571429  0.407407  0.475000   
8               XGBoost  0.428571   0.805556  0.388889  0.471306   
1         Random Forest  0.428571   0.888889  0.351852  0.438672   
0   Logistic Regression  0.285714   0.527778  0.351852  0.422222   
3              AdaBoost  0.285714   0.477778  0.333333  0.387302   
10         DecisionTree  0.214286   0.625000  0.351852  0.386555   
2     Gradient Boosting  0.285714   0.694444  0.277778  0.360195   
4          SVM (Linear)  0.285714   0.416667  0.277778  0.318627   
7        MLP Classifier  0.214286   0.400000  0.166667  0.178571   
6           Naive Bayes  0.357143   0.333333  0.111111  0.166667   

    Training Time  
9           0.094  
5           0.011  
8           0.700  
1           0.376  
0           0.607  
3           0.315  
10          0.023  
2           0.790  
4           0.107  
7           0.278  
6           0.013

### Tuning

In [11]:
def objective(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 10, 500),
        "learning_rate": trial.suggest_float("learning_rate", 1e-6, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 3, 15),
        "num_leaves": trial.suggest_int("num_leaves", 3, 255),
        "min_child_samples": trial.suggest_int("min_child_samples", 3, 100),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-8, 10.0, log=True),
        "reg_lambda": trial.suggest_float("reg_lambda", 1e-8, 10.0, log=True),
        "random_state": 42,
        "n_jobs": -1
    }

    model = OneVsRestClassifier(LGBMClassifier(**params))

    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    return f1_score(y_test, y_pred, average="macro", zero_division=0)

In [12]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

print("Tuned LGBMClassifier (MultiOutput):")
print("Accuracy:", accuracy_score(y_test, y_pred))
print("Precision:", precision_score(y_test, y_pred, average="macro", zero_division=0))
print("Recall:", recall_score(y_test, y_pred, average="macro", zero_division=0))
print("F1 Score:", f1_score(y_test, y_pred, average="macro", zero_division=0))

[I 2025-07-12 11:36:44,346] A new study created in memory with name: no-name-b6ffa6ce-5ec5-458d-9411-21ea5c8aeb72
[I 2025-07-12 11:36:44,423] Trial 0 finished with value: 0.0 and parameters: {'n_estimators': 22, 'learning_rate': 0.0003050684703029208, 'max_depth': 4, 'num_leaves': 216, 'min_child_samples': 100, 'subsample': 0.675874463564347, 'colsample_bytree': 0.8257553726560903, 'reg_alpha': 4.480723963927039, 'reg_lambda': 0.05003253213798029}. Best is trial 0 with value: 0.0.
[I 2025-07-12 11:36:44,543] Trial 1 finished with value: 0.0 and parameters: {'n_estimators': 369, 'learning_rate': 0.0002716218652094398, 'max_depth': 13, 'num_leaves': 245, 'min_child_samples': 61, 'subsample': 0.7774377339258509, 'colsample_bytree': 0.9778662292958961, 'reg_alpha': 0.003300978938756844, 'reg_lambda': 9.310729517624383}. Best is trial 0 with value: 0.0.


[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Number of positive: 39, number of negative: 98
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 137, number of used features: 0
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.284672 -> initscore=-0.921406
[LightGBM] [Info] Start training from score -0.921406
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because 

[I 2025-07-12 11:36:44,633] Trial 2 finished with value: 0.0 and parameters: {'n_estimators': 350, 'learning_rate': 0.009349437275560653, 'max_depth': 12, 'num_leaves': 173, 'min_child_samples': 69, 'subsample': 0.5568031150192192, 'colsample_bytree': 0.6713242660490883, 'reg_alpha': 1.578671704798059e-07, 'reg_lambda': 0.0001085243528917713}. Best is trial 0 with value: 0.0.


[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more 

[I 2025-07-12 11:36:44,799] Trial 3 finished with value: 0.0 and parameters: {'n_estimators': 336, 'learning_rate': 0.0004389617295238124, 'max_depth': 13, 'num_leaves': 86, 'min_child_samples': 57, 'subsample': 0.7939591321506557, 'colsample_bytree': 0.5856801834802878, 'reg_alpha': 2.1534622984295277e-08, 'reg_lambda': 0.04642152429746994}. Best is trial 0 with value: 0.0.


...

[LightGBM] [Info] Number of positive: 32, number of negative: 105
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003425 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1961
[LightGBM] [Info] Number of data points in the train set: 137, number of used features: 117
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.233577 -> initscore=-1.188224
[LightGBM] [Info] Start training from score -1.188224
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

[I 2025-07-12 11:36:55,195] Trial 48 finished with value: 0.5555555555555555 and parameters: {'n_estimators': 477, 'learning_rate': 0.09999546165117569, 'max_depth': 6, 'num_leaves': 77, 'min_child_samples': 12, 'subsample': 0.9475016058390284, 'colsample_bytree': 0.8706713419639895, 'reg_alpha': 0.018177544930761576, 'reg_lambda': 0.00014115829868225862}. Best is trial 48 with value: 0.5555555555555555.


[LightGBM] [Info] Number of positive: 39, number of negative: 98
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000417 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1946
[LightGBM] [Info] Number of data points in the train set: 137, number of used features: 111
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.284672 -> initscore=-0.921406
[LightGBM] [Info] Start training from score -0.921406
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best

[I 2025-07-12 11:36:55,442] Trial 49 finished with value: 0.5396825396825397 and parameters: {'n_estimators': 474, 'learning_rate': 0.09834411842790379, 'max_depth': 7, 'num_leaves': 84, 'min_child_samples': 9, 'subsample': 0.8674731738187578, 'colsample_bytree': 0.8631865996229748, 'reg_alpha': 0.01919294780144784, 'reg_lambda': 1.675852230235953e-05}. Best is trial 48 with value: 0.5555555555555555.


[LightGBM] [Info] Number of positive: 39, number of negative: 98
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002782 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1961
[LightGBM] [Info] Number of data points in the train set: 137, number of used features: 117
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.284672 -> initscore=-0.921406
[LightGBM] [Info] Start training from score -0.921406
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

In [13]:
joblib.dump(model, os.path.join(MODEL_PATH, f'best_lgbm-ovr_model_on_crpwarner_opcode_freq.pkl'))

['/Users/napatcholthaipanich/Dev/master/dissertation/workspace/ml/models/best_lgbm-ovr_model_on_crpwarner_opcode_freq.pkl']

### K-Fold (K=3)

In [14]:
NUM_FOLDS = 3
results = []
best_model = OneVsRestClassifier(LGBMClassifier(**study.best_params, random_state=42))
best_f1 = 0
best_fold = 0

In [15]:
for fold in range(NUM_FOLDS):
    print(f"=========== Fold-{fold} ===========")
    train_path = os.path.join(DATA_PATH, f'train_fold_{fold}-opcode-freq.csv')
    val_path = os.path.join(DATA_PATH, f'val_fold_{fold}-opcode-freq.csv')

    train_df = pd.read_csv(train_path)
    val_df   = pd.read_csv(val_path)

    X_train = train_df[feature_list]
    y_train = train_df[labels]

    X_val = val_df[feature_list]
    y_val = val_df[labels]

    # Train model
    model = OneVsRestClassifier(LGBMClassifier(**study.best_params, random_state=42))
    model.fit(X_train, y_train)

    # Evaluate
    y_pred = model.predict(X_val)
    report = classification_report(y_val, y_pred, target_names=labels, output_dict=True)
    acc = accuracy_score(y_val, y_pred)
    f1 = f1_score(y_val, y_pred, average="macro", zero_division=0)

    results.append({'fold': fold, 'accuracy': acc, 'report': report})
    print(f"Accuracy: {acc}")
    print("Precision:", precision_score(y_val, y_pred, average="macro", zero_division=0))
    print("Recall:", recall_score(y_val, y_pred, average="macro", zero_division=0))
    print("F1 Score:", f1)

    if best_f1 < f1:
        best_model = model
        best_fold = fold
## Step 6: Average Performance Summary
print("\n===== Overall Summary =====")
avg_acc = sum([r['accuracy'] for r in results]) / NUM_FOLDS
print(f"Average Accuracy: {avg_acc:.4f}")

# Save model
joblib.dump(best_model, os.path.join(MODEL_PATH, f'best_lgbm-ovr_model_on_crpwarner_opcode_freq_from_fold{best_fold}.pkl'))

=========== Fold-0 ===========
[LightGBM] [Info] Number of positive: 13, number of negative: 33
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000138 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 887
[LightGBM] [Info] Number of data points in the train set: 46, number of used features: 89
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.282609 -> initscore=-0.931558
[LightGBM] [Info] Start training from score -0.931558
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

['/Users/napatcholthaipanich/Dev/master/dissertation/workspace/ml/models/best_lgbm-ovr_model_on_crpwarner_opcode_freq_from_fold2.pkl']